# Latency measurements for warehouse_4

Conclusions:
- These metrics are useless apart from "min latency"
- Latency grows over time, as all data is fed as fast as possible (faster than it is possible to process)
- Min latency can depend on many things, average min latency would make more sense but is not possible

Future measurements:
- Run a warehouse experiment that accounts for the max throughput of each experiment scenario (similar to yolo experiment)

In [11]:
import common_utils
import os
import pandas as pd

# Example usage
root_folder = '../../../data_warehouse/minimized_warehouse_7c'
filename = 'worker1.feather'
subfolders = common_utils.find_subfolders_with_file(root_folder, filename)
print(subfolders)
prom_data_paths = {os.path.basename(x): x for x in subfolders}
yolo_data_paths = {key: os.path.join(val, "hpa_qos.feather") for key, val in prom_data_paths.items()}


['../../../data_warehouse/minimized_warehouse_7c/1738881900_(1.1000)', '../../../data_warehouse/minimized_warehouse_7c/1738915261_(1.5000)', '../../../data_warehouse/minimized_warehouse_7c/1738948257_(1.10000)']


In [12]:
from utils.header_cleaner import *
import difflib
import os


"""
Fetch paths to the data
"""


"""
Get corresponding yolo stats for each model 
"""
dfs = {}
for key in prom_data_paths.keys():
    hpa_df = pd.read_feather(yolo_data_paths[key])

    # yolo_df['total_inference_time'] = yolo_df['inf'] + yolo_df['post'] + yolo_df['pre']
    # yolo_df['end_to_end_response_time'] = yolo_df['total_inference_time'] + yolo_df['queue']
    # yolo_df['start'] = pd.to_datetime(yolo_df['start_time'], unit='ms')  # Convert to datetime (optional)
    # yolo_df.set_index('start', inplace=True)
    # resampled_df = yolo_df.resample('5s')
    model_info = common_utils.path_to_workers_and_pcl_size(key)
    dfs[model_info.resolution] = hpa_df


In [17]:
import plotly.express as px
from matplotlib import pyplot as plt

# Function to compute simple moving average
def moving_average(data, window_size):
    return data.rolling(window=window_size).mean()

# You can adjust the window size for different levels of smoothing
window_size = 3

for resolution in sorted(dfs.keys()):
    hpa_df = pd.DataFrame.from_dict(dfs[resolution])
    fig = px.line(hpa_df, x=hpa_df["timestamp"], y=hpa_df.columns)
    fig.update_layout(title=f'HPA statistics (PCL resolution: {resolution})', xaxis_title='Time', yaxis_title='Value', yaxis_type="log")
    fig.show()